In [1]:
#import statements
import numpy as np
import math
import re

#file name you'll save to
filename = 'sineCube.gcode'
#file name you'll read
readname = 'cube.gcode'

#GCODE sliced settings
    #THese are the params the input GCODE was sliced with
layerH = 0.2
width = 0.4

with open(filename, 'w') as file:
    file.write('; This code was generated by Leviticus Rhodens Non-planar code.\n')


These functions write to the output GCODE file in different ways.

In [2]:
#This cell is a collection of add to GCODE commands
def addPoint(x,y,z,e,f):
    '''This appends a new co-ordinate to the gcode file! It takes in x,y,z,and e co-ordinates as floats.'''
    
    with open(filename,'a') as file:
        if z<0:
            print("ERROR: I'm under the print bed!")
            return
        if e==0:
            file.write('G0 ')
        else:
            file.write('G1 ')
        file.write('F' + "{:#.8g}".format(f) + ' X' + "{:#.8g}".format(x) + ' Y' + "{:#.8g}".format(y) + ' Z' + "{:#.8g}".format(z) + ' E' + "{:#.8g}".format(e) + '\n')
        
def addComment(note):
    '''Takes in a string note and adds it as a comment to the GCODE file, does not need to have the ; in front'''
    with open(filename,'a') as file:
        file.write(";" + note +"\n")

def addString(string):
    '''Takes in a string and adds it to the output file, no questions asked and no notation added'''
    with open(filename,'a') as file:
        file.write(string)

These functions define the surfaces we want to interpolate between

In [3]:
#these functions define the surface maps we are transitioning between
#just make sure that the map at each point (0, z2 and z3) dosn't overlap with the other maps.
#ALso that Zhop in origonal code is higher than any non-linear function here

z2 = 100

def surface2(x,y):
    return 5*np.sin(x/2.5)*np.cos(y/5) + (y-110)/2
def surface3(x,y):
    
    return 0.01


def surface(x,y,z):
    '''This takes in the x,y, and planar z float, and returns the deltaZ from the planar z'''
    # README This is determined by YOU, and is able to change.
    
    if z<z2:
        dz = (z/z2)*surface2(x,y)
    else:
        dz = ((z-z2)/(z3-z2))*surface2(x,y)
    return dz

This function calculates the control volume of a pair of G1 commands

In [4]:
def calcControlVolume(X, Y, lastX, lastY, height, E):
    '''This Function takes in current and last co-ords, and calculates new, non-planar extrusion value.'''
    Z = height
    
    #This calculates volume of extrusion control volume and the planar volume, then finds the ratio of the two
    #This ratio is multiplied by the old extrusion value, preserving over/under extrusion in og GCODE
    #(GCODE takes a linear extrusion)
    dX = ((X-lastX)**2 + (Y-lastY)**2)**0.5
    dZ = surface(X,Y,Z) - surface(X,Y,Z-layerH)
    lastDZ = surface(lastX,lastY,Z) - surface(lastX,lastY,Z-layerH)
    vol = dX*width*(dZ + 0.5*(lastDZ-dZ)+layerH)
    oldVol = dX*width*layerH
    
    #print(E, vol, oldVol)
    
    rVol = vol/oldVol
    
    #print(e)
    
    return X, Y, Z+surface(X,Y,Z), rVol
            

These functions disect GCODE for floats

In [5]:
def extractCords(string):
    '''This function takes in a line of GCODE as a string and outputs co-ordinates in that string'''
    
    out = ['nan','nan','nan','nan','nan']
    coord = re.findall(r'[XYZEF].?\d+.\d+', string)
    
    for i in coord:
        if 'X' in i:
            out[0] = float(i[1:])
        if 'Y' in i:
            out[1] = float(i[1:])
        if 'Z' in i:
            out[2] = float(i[1:])
        if 'E' in i:
            out[3] = float(i[1:])
        if 'F' in i:
            out[4] = float(i[1:])
            
    return out
            
    

This guy puts it all together!

In [6]:
#This loop iterates over every line of text in the input GCODE, and modifies the code so movement is non planar.
#it also corrects extrusion rate

layer = 1
height = 0
lastCoords = [0,0,0,0,1200]

with open(readname) as file:
    for line in file:
        #This level is called for every line of input GCODE
        if 'G0' in line:
            coords = extractCords(line)
            
            if coords[0] == 'nan':
                coords[0] = lastCoords[0]
            if coords[1] == 'nan':
                coords[1] = lastCoords[1]
            if coords[2] == 'nan':
                coords[2] = lastCoords[2]
            if coords[3] == 'nan':
                coords[3] = lastCoords[3]
            else:
                print('G0 with E?')
            
            
            #Here we check if our path is longer than a threshold, so we dont crash into the base
            dist = ((coords[0]-lastCoords[0])**2 + (coords[1]-lastCoords[1])**2 + (coords[2]-lastCoords[2])**2)**0.5
            if dist >= 0.5:
                iterations = int(dist/0.5)
            else:
                iterations = 1
                
            lastX = lastCoords[0]
            lastY = lastCoords[1]
            
            for i in list(range(1, iterations+1)):
                t = i/iterations
                x = t*coords[0] + (1-t)*lastCoords[0]
                y = t*coords[1] + (1-t)*lastCoords[1]
                #Literally just call this for the zPt
                xPt, yPt, zPt, e = calcControlVolume(x,y,lastX,lastY,coords[2], 0)

                addPoint(x,y,zPt,0,1200)
                
                lastX = x
                lastY = y

            for i in [0,1,2,3,4]:
                if 'nan' != coords[i]:
                    lastCoords[i] = coords[i]
            
        elif 'G1' in line:
            coords = extractCords(line)
            
            if coords[0] == 'nan':
                coords[0] = lastCoords[0]
            if coords[1] == 'nan':
                coords[1] = lastCoords[1]
            if coords[2] == 'nan':
                coords[2] = lastCoords[2]
            if coords[3] == 'nan':
                coords[3] = lastCoords[3]
            #needed since O came in 
            E = coords[3] - lastCoords[3]
            if E == 0:
                #print("E is 0, e in is " + str(coords[3]))
                fish = 'fish'
                
            dist = ((coords[0]-lastCoords[0])**2 + (coords[1]-lastCoords[1])**2 + (coords[2]-lastCoords[2])**2)**0.5
            if dist >= 0.5:
                iterations = int(dist/0.5)
            else:
                iterations = 1
            
            lastX = lastCoords[0]
            lastY = lastCoords[1]
            
            for i in list(range(1, iterations+1)):
                
                t = i/iterations
                x = t*coords[0] + (1-t)*lastCoords[0]
                y = t*coords[1] + (1-t)*lastCoords[1]
                
                xPt, yPt, zPt, rVol = calcControlVolume(x,y,lastX,lastY,coords[2], E/iterations)
                e = rVol*E/iterations
                print(rVol,E,iterations,e)
                addPoint(xPt, yPt, zPt, e, 1200)
                
                #print(t, E/iterations, e)
                
                lastX = x
                lastY = y
                
            for i in [0,1,2,3,4]:
                    if 'nan' != coords[i]:
                        lastCoords[i] = coords[i]
        
        elif 'LAYER:' in line:
            layer += 1
            height = (layer-1)*layerH
            addString(line)
        elif 'M82' in line:
            print('Die filthy global etrusion!')
        else:
            addString(line)
            
        

Die filthy global etrusion!
nan 0 4 nan
nan 0 4 nan
nan 0 4 nan
nan 0 4 nan
0.45033332345687793 0 3 0.0
0.45099991111400817 0 3 0.0
0.45166632101179605 0 3 0.0
0.45324447220672565 0 400 0.0
0.4557245440997209 0 400 0.0
0.4581848870007692 0 400 0.0
0.4606258971504946 0 400 0.0
0.4630481639559812 0 400 0.0
0.46545246410161367 0 400 0.0
0.46783975378870274 0 400 0.0
0.4702111591814377 0 400 0.0
0.47256796515462685 0 400 0.0
0.47491160245565217 0 400 0.0
0.47724363340891546 0 400 0.0
0.4795657363056083 0 400 0.0
0.4818796886347821 0 400 0.0
0.4841873493232647 0 400 0.0
0.4864906401618775 0 400 0.0
0.488791526603538 0 400 0.0
0.4910919981251028 0 400 0.0
0.49339404834917305 0 400 0.0
0.49569965512447633 0 400 0.0
0.4980107607638561 0 400 0.0
0.5003292526373235 0 400 0.0
0.50265694431408 0 400 0.0
0.5049955574419341 0 400 0.0
0.507346704545165 0 400 0.0
0.5097118729127125 0 400 0.0
0.5120924097376791 0 400 0.0
0.5144895086566202 0 400 0.0
0.5169041978231236 0 400 0.0
0.519337329634837 0 400 

/tmp/ipykernel_303/977854913.py:16: RuntimeWarning: invalid value encountered in scalar divide
  rVol = vol/oldVol


1.0141080023496818 0.7783699999999953 46 0.017159809691063416
1.0202002906495466 0.7783699999999953 46 0.017262897831149628
1.0256420904582462 0.7783699999999953 46 0.017354978998912616
1.0302688811778966 0.7783699999999953 46 0.01743326932700945
1.0339592701193827 0.7783699999999953 46 0.01749571471919172
1.036640575089681 0.7783699999999953 46 0.01754108531375109
1.038292119245269 0.7783699999999953 46 0.01756903123602033
1.0389460857091346 0.7783699999999953 46 0.01758009705942205
1.0386858928335188 0.7783699999999953 46 0.017575694313148288
1.0376421661877029 0.7783699999999953 46 0.017558033323815597
1.0359864950131397 0.7783699999999953 46 0.017530017567899406
1.0339232638343154 0.7783699999999953 46 0.017495105453711114
1.0316799393647502 0.7783699999999953 46 0.017457145965289907
1.0294962646516048 0.7783699999999953 46 0.01742019581558402
1.027612863226648 0.7783699999999953 46 0.017388326616298286
1.0262597835165443 0.7783699999999953 46 0.01736543103686452
1.0256455166355605

1.0460562580331565 0.8162799999999919 49 0.017426016373618295
1.0433233203142551 0.8162799999999919 49 0.01738048897767575
1.0408295615584617 0.8162799999999919 49 0.01733894601038638
1.0387877901634184 0.8162799999999919 49 0.0173049325990732
1.0373856487392055 0.8162799999999919 49 0.017281574639853678
1.036777091972596 0.8162799999999919 49 0.017271436829293517
1.0370754046098891 0.8162799999999919 49 0.01727640635255004
1.0383480739315272 0.8162799999999919 49 0.01729760746507793
1.040613747541043 0.8162799999999919 49 0.01733535081311825
1.043841413355724 0.8162799999999919 49 0.017389119773346978
1.0479518385930853 0.8162799999999919 49 0.017457594424627656
1.0528212027992165 0.8162799999999919 49 0.01753871206981502
1.058286761140137 0.8162799999999919 49 0.017629761579254336
1.0641542827218053 0.8162799999999919 49 0.017727507304084626
1.070206928733198 0.8162799999999919 49 0.017828336975231146
1.076215170318013 0.8162799999999919 49 0.01792842692300365
1.0819472991938213 0.81

nan 5.0 1 nan
1.0556715906950511 0.6252899999999926 37 0.017840564566100017
1.0640693735732791 0.6252899999999926 37 0.017982484827071023
1.0733081998788223 0.6252899999999926 37 0.018138618494654618
1.083007745779308 0.6252899999999926 37 0.01830253819887393
1.0927687215438606 0.6252899999999926 37 0.01846749605119331
1.1021893086310666 0.6252899999999926 37 0.01862670142686247
1.110881700877489 0.6252899999999926 37 0.018773600506531804
1.1184880688551995 0.6252899999999926 37 0.018902146069579982
1.1246952902125003 0.6252899999999926 37 0.01900704643289097
1.1292478396113326 0.6252899999999926 37 0.019083983287312478
1.1319583076365634 0.6252899999999926 37 0.019129789464379952
1.132715115657663 0.6252899999999926 37 0.01914257931539383
1.1314871090541814 0.6252899999999926 37 0.019121826335688666
1.1283248397211498 0.6252899999999926 37 0.01906838483862782
1.1233584850590261 0.6252899999999926 37 0.01898445478709595
1.1167924891146572 0.6252899999999926 37 0.018873491230229616
1.10

...

1.0540172727149648 0.26188999999999396 15 0.01840243890342105
1.054861250438291 0.00705999999991036 1 0.0074473204279997774
1.0554357384529347 0.05318000000011125 3 0.018709357523681493
1.0559978224850666 0.05318000000011125 3 0.018719321399957772
1.0560521649874468 0.05318000000011125 3 0.018720284711383303
1.0559014373736288 0.005459999999857246 1 0.005765221847909279
1.0558220909980112 0.0024200000000291766 1 0.0025550894602459923
1.0552255197571967 0.1731600000000526 10 0.018272285100121168
1.053249326725562 0.1731600000000526 10 0.018238065341585372
1.049667710773058 0.1731600000000526 10 0.018176046079751797
1.0446356292420078 0.1731600000000526 10 0.018088910555960104
1.0383706933176218 0.1731600000000526 10 0.0179804269254934
1.0311437602875897 0.1731600000000526 10 0.017855285353145327
1.0232672261401035 0.1731600000000526 10 0.017718895287847414
1.0150815245353917 0.1731600000000526 10 0.017577151678860183
1.0069404156339834 0.1731600000000526 10 0.01743618023712335
0.9991957

1.0245638690854 0.26188999999999396 15 0.01788820211165128
1.0334216379482508 0.26188999999999396 15 0.01804285285081741
1.0410986100067878 0.26188999999999396 15 0.018176887664978093
1.0472575092512006 0.26188999999999396 15 0.018284417939852707
1.0516277396507758 0.26188999999999396 15 0.018360719249142354
1.0540172727149644 0.26188999999999396 15 0.018402438903421043
1.0548612504382902 0.00705999999991036 1 0.007447320427999771
1.0554357384529336 0.05318000000011125 3 0.018709357523681476
1.0559978224850655 0.05318000000011125 3 0.018719321399957755
1.0560521649874457 0.05318000000011125 3 0.018720284711383282
1.055901437373627 0.005460000000084619 1 0.005765221848149354
1.0558220909980096 0.002419999999801803 1 0.002555089460005922
1.055225519757196 0.17315000000007785 10 0.018271229874604063
1.0532493267255612 0.17315000000007785 10 0.01823701209226129
1.0496677107730572 0.17315000000007785 10 0.018174996412043655
1.0446356292420071 0.17315000000007785 10 0.018087865920333488
1.03

1.0188411220462912 0.16805999999996857 10 0.017122643897106767
1.0151421083041003 0.27282000000013795 16 0.017309441874229045
1.0178336726871797 0.27282000000013795 16 0.01735533641141605
1.0213124658354829 0.27282000000013795 16 0.017414654183086083
1.0253832872285116 0.27282000000013795 16 0.017484066776364
1.0298190521527586 0.27282000000013795 16 0.017559702113028604
1.0343712285247022 0.27282000000013795 16 0.017637322410390746
1.0387813066506677 0.27282000000013795 16 0.017712519755036155
1.0427927627345097 0.27282000000013795 16 0.0177809200955858
1.04616295355463 0.27282000000013795 16 0.017838386061807404
1.0486743828451532 0.27282000000013795 16 0.01788120907049746
1.0501448093860744 0.27282000000013795 16 0.017906281681053356
1.0504357212459994 0.27282000000013795 16 0.017911242091904905
1.049458777464259 0.27282000000013795 16 0.017894583979246495
1.0471799140866196 0.27282000000013795 16 0.017855726510078503
1.0436209213753078 0.27282000000013795 16 0.017795041235609717
1.

1.0007933815263126 0.6519000000000688 39 0.016728646292745435
0.9919499661544388 0.6519000000000688 39 0.016580825203490943
0.982967602008639 0.6519000000000688 39 0.016430681532038444
0.9742080574162378 0.6519000000000688 39 0.01628426237512083
0.9660241265574606 0.6519000000000688 39 0.01614746482315064
0.958745420537987 0.6519000000000688 39 0.01602579845253281
0.9526650921691489 0.6519000000000688 39 0.015924163425259836
0.9480280291205921 0.6519000000000688 39 0.015846653132917415
0.9450209909709241 0.6519000000000688 39 0.015796389333692575
0.9437650873906007 0.6519000000000688 39 0.015775396422307627
0.9443109004012542 0.6519000000000688 39 0.015784519896708784
0.9466364471644357 0.6519000000000688 39 0.01582339230529643
0.950648065349275 0.6519000000000688 39 0.015890448046186098
0.95618418542051 0.6519000000000688 39 0.015982986422453747
0.9630218379164791 0.6519000000000688 39 0.01609728041379023
0.9708856336338354 0.6519000000000688 39 0.016228726783742667
0.9794588550384294

1.03613661168699 0.0795900000000529 4 0.020616528231055583
1.032254847315917 0.0795900000000529 4 0.02053929082448211
1.0400807179001266 0.07958000000007814 4 0.020692405882643337
1.042492469066094 0.07958000000007814 4 0.020740387672090306
1.0433132487367296 0.07958000000007814 4 0.02075671708363762
1.0424119341082445 0.07958000000007814 4 0.02073878542910389
1.0428226757650974 0.0795900000000529 4 0.020749564191049816
1.0455932568681365 0.0795900000000529 4 0.020804691828547574
1.0466020798164912 0.0795900000000529 4 0.020824764883162473
1.045888220474687 0.0795900000000529 4 0.02081056086690892
1.0494014189264558 0.07958999999982552 4 0.02088046473304338
1.0482701809998654 0.07958999999982552 4 0.020857955926399097
1.045372165466252 0.07958999999982552 4 0.020800292662319152
1.04076249611721 0.07958999999982552 4 0.020708571766446787
1.0363336247987915 0.07958000000007814 4 0.020617857465392204
1.0426550584765297 0.07958000000007814 4 0.020743622388410928
1.0474023027400354 0.079580